<a href="https://colab.research.google.com/github/huanyanwei/ai-projects/blob/main/NLP_Project_Part_2.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Part 3: RNN/ LSTM ##

**Imports**

In [ ]:
%matplotlib inline
import matplotlib.pyplot as plt
import keras
from keras.datasets import mnist
from keras.models import Sequential, Model
from keras.layers import Dense, Dropout, Flatten, Input
from keras.layers import Conv2D, MaxPooling2D
from keras.optimizers import RMSprop
from keras.callbacks import ModelCheckpoint, Callback, TensorBoard
from keras.callbacks import LambdaCallback
from keras import backend as K

import tensorflow as tf
print(tf.__version__)

2.2.0


In [ ]:
import numpy as np
import os
import time
import functools

**Import Data**

In [ ]:
# Opening the log file to save
with open('/content/drive/My Drive/NLP/Triage-TokenSize__Core.ps1', 'r') as f:
    raw_logs = f.read().splitlines()

print("There are total", len(raw_logs) ,"lines of logs in this data set.")

There are total 3994 lines of logs in this data set.


In [ ]:
# Join our list of logs into a single string containing all logs
raw_logs_joined = "\n\n".join(raw_logs) 
#print(raw_logs_joined)

# Find all unique characters in the joined logs
# We will form new logs based on each char added in one by one. Not word by word...
vocab = sorted(set(raw_logs_joined))
print("There are", len(vocab), "unique characters in the dataset")
print(vocab)

There are 96 unique characters in the dataset
['\t', '\n', ' ', '!', '"', '#', '$', '%', '&', "'", '(', ')', '*', '+', ',', '-', '.', '/', '0', '1', '2', '3', '4', '5', '6', '7', '8', '9', ':', ';', '<', '=', '>', '?', '@', 'A', 'B', 'C', 'D', 'E', 'F', 'G', 'H', 'I', 'J', 'K', 'L', 'M', 'N', 'O', 'P', 'Q', 'R', 'S', 'T', 'U', 'V', 'W', 'X', 'Y', 'Z', '[', '\\', ']', '_', '`', 'a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u', 'v', 'w', 'x', 'y', 'z', '{', '|', '}', '�']


In [ ]:
### Define numerical representation of text ###

# Create a mapping from character to unique index.
# For example, to get the index of the character "d", 
#   we can evaluate `char2idx["d"]`.  
char2idx = {u:i for i, u in enumerate(vocab)}
print(char2idx)

# Create a mapping from indices to characters. This is
#   the inverse of char2idx and allows us to convert back
#   from unique index to the character in our vocabulary.
idx2char = np.array(vocab)
print(idx2char)

{'\t': 0, '\n': 1, ' ': 2, '!': 3, '"': 4, '#': 5, '$': 6, '%': 7, '&': 8, "'": 9, '(': 10, ')': 11, '*': 12, '+': 13, ',': 14, '-': 15, '.': 16, '/': 17, '0': 18, '1': 19, '2': 20, '3': 21, '4': 22, '5': 23, '6': 24, '7': 25, '8': 26, '9': 27, ':': 28, ';': 29, '<': 30, '=': 31, '>': 32, '?': 33, '@': 34, 'A': 35, 'B': 36, 'C': 37, 'D': 38, 'E': 39, 'F': 40, 'G': 41, 'H': 42, 'I': 43, 'J': 44, 'K': 45, 'L': 46, 'M': 47, 'N': 48, 'O': 49, 'P': 50, 'Q': 51, 'R': 52, 'S': 53, 'T': 54, 'U': 55, 'V': 56, 'W': 57, 'X': 58, 'Y': 59, 'Z': 60, '[': 61, '\\': 62, ']': 63, '_': 64, '`': 65, 'a': 66, 'b': 67, 'c': 68, 'd': 69, 'e': 70, 'f': 71, 'g': 72, 'h': 73, 'i': 74, 'j': 75, 'k': 76, 'l': 77, 'm': 78, 'n': 79, 'o': 80, 'p': 81, 'q': 82, 'r': 83, 's': 84, 't': 85, 'u': 86, 'v': 87, 'w': 88, 'x': 89, 'y': 90, 'z': 91, '{': 92, '|': 93, '}': 94, '�': 95}
['\t' '\n' ' ' '!' '"' '#' '$' '%' '&' "'" '(' ')' '*' '+' ',' '-' '.' '/'
 '0' '1' '2' '3' '4' '5' '6' '7' '8' '9' ':' ';' '<' '=' '>' '?' '@

In [ ]:
### Vectorize the logs string ###
from numpy import array
import array as arr 

def vectorize_string(string):
  vectorized_output = np.array([char2idx[char] for char in string])
  return vectorized_output


vectorized_logs = np.asarray(vectorize_string(raw_logs_joined))
print(vectorized_logs)


[ 5  5  2 ... 36 21  4]


In [ ]:
### Batch definition to create training examples ###

def get_batch(vectorized_logs, seq_length, batch_size):
  # the length of the vectorized logs string
  n = vectorized_logs.shape[0] - 1
  # randomly choose the starting indices for the examples in the training batch
  idx = np.random.choice(n-seq_length, batch_size)
  print(idx)

  # append output into the vector in each iteration
  input_batch = [vectorized_logs[i : i+seq_length] for i in idx]
  print(input_batch)

  output_batch = [vectorized_logs[i+1 : i+seq_length+1] for i in idx]
  #print(output_batch)

  # x_batch, y_batch provide the true inputs and targets for network training
  x_batch = np.reshape(input_batch, [batch_size, seq_length])
  y_batch = np.reshape(output_batch, [batch_size, seq_length])
  return x_batch, y_batch

In [ ]:
def LSTM(rnn_units): 
  return tf.keras.layers.LSTM(
    rnn_units, 
    return_sequences=True, 
    recurrent_initializer='glorot_uniform',
    recurrent_activation='sigmoid',
    stateful=True,
  )

In [ ]:
### Defining the RNN Model ###
from tensorflow.keras.layers import Dense

def build_model(vocab_size, embedding_dim, rnn_units, batch_size):
  model = tf.keras.Sequential([
    # Layer 1: Embedding layer to transform indices into dense vectors 
    #   of a fixed embedding size
    tf.keras.layers.Embedding(vocab_size, embedding_dim, batch_input_shape=[batch_size, None]),

    # Layer 2: LSTM with `rnn_units` number of units. 
    # TODO: Call the LSTM function defined above to add this layer.
    LSTM(rnn_units),

    # Layer 3: Dense (fully-connected) layer that transforms the LSTM output
    #   into the vocabulary size. 
    # TODO: Add the Dense layer.
    Dense(vocab_size)
  ])

  return model

# Build a simple model with default hyperparameters. You will get the 
#   chance to change these later.
model = build_model(len(vocab), embedding_dim=256, rnn_units=1024, batch_size=32)

In [ ]:
model.summary()

Model: "sequential_1"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding_1 (Embedding)      (32, None, 256)           24576     
_________________________________________________________________
lstm_1 (LSTM)                (32, None, 1024)          5246976   
_________________________________________________________________
dense_1 (Dense)              (32, None, 96)            98400     
Total params: 5,369,952
Trainable params: 5,369,952
Non-trainable params: 0
_________________________________________________________________


In [ ]:
x, y = get_batch(vectorized_logs, seq_length=100, batch_size=32)
pred = model(x)
print("Input shape:      ", x.shape, " # (batch_size, sequence_length)")
print("Prediction shape: ", pred.shape, "# (batch_size, sequence_length, vocab_size)")

[127200    470  87831  48759  51933  64718  73855  57662 127715 106609
  60785  91388   9698 125923  65214  33110 100378  83287  38169  62420
 101490  91370   5463 142481  42025 105925   5371  88121 128732   7508
  80951  32374]
[array([74, 85, 73,  2, 84, 74, 85, 70,  2, 77, 74, 79, 76, 84,  2, 85, 80,
        2,  4, 42, 51,  4,  2, 66, 83, 70,  2, 85, 83, 74, 70, 69, 14,  2,
       74, 71,  2, 85, 73, 66, 85,  2, 66, 77, 84, 80,  2, 83, 70, 85, 86,
       83, 79, 84,  2, 79, 80,  1,  1,  5,  0,  0, 83, 70, 84, 86, 77, 85,
       84, 14,  2, 85, 73, 70, 79,  2, 66, 77, 77,  2, 84, 74, 85, 70, 84,
        2, 66, 83, 70,  2, 85, 83, 74, 70, 69, 16,  1,  1,  5,  0]), array([48, 39, 53, 53,  2, 40, 49, 52,  2, 35,  2, 50, 35, 52, 54, 43, 37,
       55, 46, 35, 52,  2, 50, 55, 52, 50, 49, 53, 39, 16,  2,  2, 57, 70,
        2, 72, 83, 66, 79, 85,  2, 59, 80, 86,  2, 66,  2, 79, 80, 79, 70,
       89, 68, 77, 86, 84, 74, 87, 70, 14,  2,  1,  1,  5,  5,  2, 83, 80,
       90, 66, 77, 85, 90,

In [ ]:
# Sampling out for the first example in the batch
sampled_indices = tf.random.categorical(pred[0], num_samples=1)
sampled_indices = tf.squeeze(sampled_indices,axis=-1).numpy()

# Decode these to see the text predicted by the untrained model:
print("Input: \n", repr("".join(idx2char[x[0]])))
print()
print("Next Char Predictions: \n", repr("".join(idx2char[sampled_indices])))

Input: 
 'ith site links to "HQ" are tried, if that also returns no\n\n#\t\tresults, then all sites are tried.\n\n#\t'

Next Char Predictions: 
 'pr8(c -f\t;o6\nm}%c]Kf0_v�"Z,6eSP(Z3#ZyA*vy|%,#SXf/5ujtA58y1 -W6�]M,/I(5o`o;F\nS_4Do\'uoc)g6K#agW/*pJ]S\t'


In [ ]:
### Defining the loss function ###

def compute_loss(labels, logits):
  loss = tf.keras.losses.sparse_categorical_crossentropy(labels, logits, from_logits=True) # TODO
  return loss

example_batch_loss = compute_loss(y, pred) # TODO

print("Prediction shape: ", pred.shape, " # (batch_size, sequence_length, vocab_size)") 
print("scalar_loss:      ", example_batch_loss.numpy().mean())

Prediction shape:  (32, 100, 96)  # (batch_size, sequence_length, vocab_size)
scalar_loss:       4.5640306


In [ ]:
### Hyperparameter setting and optimization ###
## Can be adjusted ##

# Optimization parameters:
num_training_iterations = 2000  # Increase this to train longer
batch_size = 4  # Experiment between 1 and 64
seq_length = 100  # Experiment between 50 and 500
learning_rate = 5e-3  # Experiment between 1e-5 and 1e-1

# Model parameters: 
vocab_size = len(vocab)
embedding_dim = 256 
rnn_units = 1024  # Experiment between 1 and 2048

# Checkpoint location: 
checkpoint_dir = './training_checkpoints'
checkpoint_prefix = os.path.join(checkpoint_dir, "my_ckpt")

In [ ]:
# Download and import the MIT 6.S191 package
!pip install mitdeeplearning
import mitdeeplearning as mdl

     |████████████████████████████████| 2.1MB 2.8MB/s 
  Created wheel for mitdeeplearning: filename=mitdeeplearning-0.1.2-cp36-none-any.whl size=2114586 sha256=dbf9710020910ae0bd8b1f840423d51a4588c5449626a107e0742bfd23bb79dd
  Stored in directory: /root/.cache/pip/wheels/27/e1/73/5f01c787621d8a3c857f59876c79e304b9b64db9ff5bd61b74
Successfully built mitdeeplearning


In [ ]:
from IPython import display as ipythondisplay
from tqdm import tqdm
!apt-get install abcmidi timidity > /dev/null 2>&1

In [ ]:
### Define optimizer and training operation ###

'''TODO: instantiate a new model for training using the `build_model`
  function and the hyperparameters created above.'''
# build_model(vocab_size, embedding_dim, rnn_units, batch_size):
model = build_model(vocab_size, embedding_dim, rnn_units, batch_size)

'''TODO: instantiate an optimizer with its learning rate.
  Checkout the tensorflow website for a list of supported optimizers.
  https://www.tensorflow.org/api_docs/python/tf/keras/optimizers/
  Try using the Adam optimizer to start.'''
optimizer = tf.keras.optimizers.Adam(learning_rate)

@tf.function
def train_step(x, y): 
  # Use tf.GradientTape()
  with tf.GradientTape() as tape:
  
    '''TODO: feed the current input into the model and generate predictions'''
    y_hat = model(x)
  
    '''TODO: compute the loss!'''
    loss = compute_loss(y, y_hat)

  # Now, compute the gradients 
  '''TODO: complete the function call for gradient computation. 
      Remember that we want the gradient of the loss with respect all 
      of the model parameters. 
      HINT: use `model.trainable_variables` to get a list of all model
      parameters.'''
  grads = tape.gradient(loss, model.trainable_variables)
  
  # Apply the gradients to the optimizer so it can update the model accordingly
  optimizer.apply_gradients(zip(grads, model.trainable_variables))
  return loss

if hasattr(tqdm, '_instances'): tqdm._instances.clear() # clear if it exists

for iter in tqdm(range(num_training_iterations)):

  # Grab a batch and propagate it through the network
  x_batch, y_batch = get_batch(vectorized_logs, seq_length, batch_size)
  loss = train_step(x_batch, y_batch)

  # Update the model with the changed weights!
  if iter % 100 == 0:     
    model.save_weights(checkpoint_prefix)
    
# Save the trained model and the weights
model.save_weights(checkpoint_prefix)

  0%|          | 0/2000 [00:00<?, ?it/s]

[ 99163 123820 115827  67368]
[array([ 6, 84, 68, 83, 74, 81, 85, 28, 68, 86, 83, 83, 70, 79, 85, 36, 66,
       84, 70, 50, 83, 74, 79, 68, 74, 81, 66, 77, 54, 90, 81, 70,  1,  1,
        0, 35, 69, 69, 15, 47, 70, 78, 67, 70, 83,  2, 15, 74, 79, 81, 86,
       85, 49, 67, 75, 70, 68, 85,  2,  6, 84, 81, 70, 68, 74, 66, 77, 40,
       53, 50, 81, 83, 80, 85, 80, 36, 66, 84, 70, 50, 83, 74, 79, 68, 74,
       81, 66, 77,  2, 15, 47, 70, 78, 67, 70, 83, 54, 90, 81, 70]), array([73, 66, 87, 74, 80, 83,  1,  1,  0,  5,  5,  1,  1,  0,  6, 83, 70,
       84, 86, 77, 85, 35,  2, 31,  2,  6, 79, 86, 77, 77,  1,  1,  0,  5,
        6, 71, 74, 83, 84, 85, 50, 66, 72, 70,  2, 31,  2,  6, 79, 86, 77,
       77,  1,  1,  0,  5,  6, 78, 80, 83, 70, 50, 66, 72, 70, 84, 50, 70,
       79, 69, 74, 79, 72,  2, 31,  2,  6, 79, 86, 77, 77,  1,  1,  0,  6,
       68, 86, 83, 83, 70, 79, 85, 52, 70, 85, 83, 90, 37, 80, 86]), array([80, 78, 66, 74, 79, 53, 68, 80, 81, 70, 37, 80, 79, 85, 83, 80, 77,
      

  0%|          | 6/2000 [00:01<30:06,  1.10it/s]

[55153  1000 87343 73826]
[array([46, 41,  4, 11,  2, 15, 80, 83,  1,  1,  0,  0,  0,  0,  0, 10,  6,
       64, 16, 81, 83, 74, 79, 68, 74, 81, 66, 77, 54, 90, 81, 70,  2, 15,
       77, 74, 76, 70,  2,  4, 38, 46, 41, 53,  4, 11,  1,  1,  0,  0,  0,
        0, 94, 92,  1,  1,  0,  0,  0,  0,  0, 67, 83, 70, 66, 76,  1,  1,
        0,  0,  0,  0, 94,  1,  1,  0,  0,  0,  0,  5, 68, 80, 79, 69, 74,
       85, 74, 80, 79,  2, 85, 80,  2, 71, 74, 79, 69,  2, 22, 18]), array([81, 77, 74, 70, 83, 84,  2, 71, 83, 80, 78,  2, 66, 79, 69,  2, 66,
       72, 66, 74, 79, 84, 85,  2, 66, 79, 90,  2, 68, 77, 66, 74, 78, 84,
        2,  1,  1,  5,  5,  2, 80, 83,  2, 77, 66, 88, 84, 86, 74, 85, 84,
       14,  2, 74, 79, 68, 77, 86, 69, 74, 79, 72,  2, 66, 85, 85, 80, 83,
       79, 70, 90, 84, 95,  2, 71, 70, 70, 84, 14,  2, 85, 73, 66, 85,  2,
       66, 83, 74, 84, 70,  2, 80, 83,  2, 83, 70, 84, 86, 77, 85]), array([ 1,  1,  0,  5,  5,  2, 54, 49, 38, 49, 28,  2, 69, 70, 84, 68, 83,
       74,

  1%|          | 16/2000 [00:01<15:03,  2.20it/s]

...

[ 50321 130865 117755  39939]
[array([77, 85, 84, 16, 54, 70, 77, 70, 78, 70, 85, 83, 90, 16, 54, 41, 53,
       39, 89, 81, 66, 79, 84, 74, 80, 79, 52, 35, 47, 37, 66, 68, 73, 70,
       52, 80, 88, 84, 55, 84, 70, 69, 13, 13,  1,  1,  0,  0,  0,  0,  0,
       94,  1,  1,  0,  0,  0,  0,  0, 39, 46, 53, 39, 92,  1,  1,  0,  0,
        0,  0,  0,  0,  5,  5,  2, 85, 73, 70,  2, 52, 35, 47,  2, 68, 66,
       68, 73, 70,  2, 73, 66, 84,  2, 67, 70, 70, 79,  2, 70, 89]), array([66, 77, 77, 90,  2, 84, 81, 70, 68, 74, 71, 74, 70, 69,  2, 88, 66,
       84,  2, 66,  2, 73, 86, 67,  2, 84, 74, 85, 70, 14,  2, 85, 73, 74,
       84,  2, 78, 66, 90,  2, 85, 66, 76, 70,  2, 66,  2, 77, 80, 79, 72,
        2, 85, 74, 78, 70,  4,  1,  1,  1,  1,  0,  0,  0,  6, 69, 74, 83,
       70, 68, 85, 53, 74, 85, 70, 46, 74, 79, 76, 84, 31, 34, 10,  1,  1,
        0,  0,  0,  0, 74, 79, 87, 80, 76, 70, 15, 84, 69, 84, 81]), array([ 2,  6, 70, 89, 68, 70, 81, 85, 74, 80, 79,  2, 85, 80,  2, 67, 70,
      

100%|█████████▉| 1996/2000 [00:46<00:00, 44.90it/s]

[  4378  30206   7545 111726]
[array([ 2, 66, 71, 85, 70, 83,  2, 84, 86, 74, 85, 66, 67, 74, 77, 74, 85,
       90,  2, 85, 70, 84, 85, 84,  4,  1,  1,  0, 94,  1,  1,  2,  2,  2,
        2,  1,  1,  2,  2,  2,  2,  5,  5, 34,  5, 34,  5, 81, 70, 83, 71,
       88, 81,  2,  6, 78, 90, 74, 79, 87, 80, 68, 66, 85, 74, 80, 79, 16,
       78, 90, 68, 80, 78, 78, 66, 79, 69, 16, 79, 66, 78, 70,  2, 15, 69,
        1,  1,  0,  1,  1,  0, 57, 83, 74, 85, 70, 15, 42, 80, 84]), array([70, 38, 80, 78, 66, 74, 79,  2, 65,  1,  1,  0,  0,  0,  0, 15, 56,
       66, 77, 86, 70,  2, 34, 92, 94,  1,  1,  0,  0,  0, 35, 69, 69, 15,
       47, 70, 78, 67, 70, 83,  2, 65,  1,  1,  0,  0,  0,  0, 15, 74, 79,
       81, 86, 85, 49, 67, 75, 70, 68, 85,  2,  6, 81, 83, 80, 85, 80, 36,
       66, 84, 70, 50, 83, 74, 79, 68, 74, 81, 66, 77,  2, 65,  1,  1,  0,
        0,  0,  0, 15, 47, 70, 78, 67, 70, 83, 54, 90, 81, 70,  2]), array([ 0,  5,  5,  2, 83, 70, 81, 70, 66, 85,  2, 84, 74, 78, 74, 77, 66,
      

100%|██████████| 2000/2000 [00:46<00:00, 42.98it/s]

[132548  67218  34485  44316]
[array([70, 77,  2, 85, 73, 66, 85,  2, 74, 79, 69, 74, 68, 66, 85, 70, 84,
        2, 88, 70,  2, 84, 73, 80, 86, 77, 69,  2, 76, 70, 70, 81,  2, 85,
       83, 90, 74, 79, 72,  2, 85, 80,  2, 71, 74, 79, 69,  2, 66,  2, 38,
       37, 14,  2, 74, 85,  2, 74, 84,  2, 85, 80, 80,  2, 77, 66, 85, 70,
        1,  1,  0,  0,  5,  5,  2, 85, 80,  2, 72, 80,  2, 67, 66, 68, 76,
        2, 71, 83, 80, 78,  2, 73, 70, 83, 70, 16,  1,  1,  0,  0]), array([67, 54, 76, 85, 64, 43, 43, 53, 23, 38, 70, 71, 66, 86, 77, 85, 16,
       57, 66, 83, 79, 37, 80, 86, 79, 85, 13, 13,  1,  1,  0,  0,  0,  0,
        6, 68, 86, 83, 83, 70, 79, 85, 36, 66, 84, 70, 50, 83, 74, 79, 68,
       74, 81, 66, 77, 16, 45, 83, 67, 54, 76, 85, 64, 43, 43, 53, 23, 38,
       70, 71, 66, 86, 77, 85,  2, 31,  2,  4, 57, 66, 83, 79,  4,  1,  1,
        0,  0,  0, 94,  0,  1,  1,  0,  0, 94,  1,  1,  0,  0, 53]), array([49, 71, 40, 83, 80, 78, 37, 66, 68, 73, 70,  4,  1,  1,  0,  0,  0,
      

In [ ]:
model = build_model(vocab_size, embedding_dim, rnn_units, batch_size=1)

# Restore the model weights for the last checkpoint after training
model.load_weights(tf.train.latest_checkpoint(checkpoint_dir))
model.build(tf.TensorShape([1, None]))

model.summary()

Model: "sequential_4"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding_4 (Embedding)      (1, None, 256)            24576     
_________________________________________________________________
lstm_4 (LSTM)                (1, None, 1024)           5246976   
_________________________________________________________________
dense_4 (Dense)              (1, None, 96)             98400     
Total params: 5,369,952
Trainable params: 5,369,952
Non-trainable params: 0
_________________________________________________________________


In [ ]:
### Prediction of a generated log ###

def generate_text(model, start_string, generation_length=1000):
  # Evaluation step (generating ABC text using the learned RNN model)

  # Convert the start string to numbers (vectorize)
  input_eval = [char2idx[i] for i in start_string]
  input_eval = tf.expand_dims(input_eval, 0)

  text_generated = []

  model.reset_states()
  tqdm._instances.clear()

  for i in tqdm(range(generation_length)):
      # Evaluate the inputs and generate the next character predictions'''
      predictions = model(input_eval)
      
      # Remove the batch dimension
      predictions = tf.squeeze(predictions, 0)
      
      predicted_id = tf.random.categorical(predictions, num_samples=1)[-1,0].numpy()
      
      # Pass the prediction along with the previous hidden state
      #   as the next inputs to the model
      input_eval = tf.expand_dims([predicted_id], 0)
      
      text_generated.append(idx2char[predicted_id])
    
  return (start_string + ''.join(text_generated))

In [ ]:
# Use the model and the function defined above to generate ABC format text of length 500 char. 
# Assume that each log will not be more than 500 char. 
# start_string with a random IP address/ number since we know that the logs will always start with number
generated_text = generate_text(model, start_string="1", generation_length=10000) 

100%|██████████| 10000/10000 [00:44<00:00, 225.85it/s]


In [ ]:
print(generated_text)

1640-444-40cb5a9d.substring1.316319 /}}

		#Wrappe:prefixTokenLengths.attributes.and FSPs base rangion and wrong the mater"

		## For sort





#############

function Ensure-trie2path "USER"

		foreach ( $errorRecord )

				Add-Member -InputObject $property -Name estimatedSiteLergestTable.count -Name erfwayPointtables.$tableName.last\pserfwalizeUser + $TGTRAPIDsFilterAnsionTokencTink will regord 

	#for able

	than is ues atains an rererryshory = @{ bject System.Management.Automation.ErrorCodjects ;

	}

	

	$script:masterResults.Telemetry.FullyExpands.

				}

	$script:evoinSID = 0 ; 

				$protoTokenDiskCacheGroupsOnly__TrapA", 

			"NotSStempTGSIDKey = $prefixTokenLengths=21,

		$notemType.preferr.WarnThresholds.KrbTkt_OSMaxTokenSizeMaxConfig,Largestrongement.Automation.ErrorRecord ( 

		$_ -eq 51) -eq 52) -or ($ntDSPSearch -computerName will f

## do reacKe keep donally        's wroup next ras to chech

	############################



	##Note:protoInitialFilterString DN of group

## Conclusion

Both GPT-2 and LSTM seems to able to recognise some of the pattern commonly found in PowerShell structure, e.g. alignment and naming conventions. Unfortunately, it also seems that both models did not manage to write something that makes sense. It may be due to only inputting 1 file into into the model, which is too limited. Furthermore, GPT-2 is trained based on English words, hence it is unable to perform as good as predicting English words. 